In [2]:
# coding=gbk

from __future__ import absolute_import,print_function,unicode_literals,division

import tensorflow as tf
import tensorflow.keras as keras
import numpy as np
import pandas as pd
import pandas_profiling
import unicodedata
import matplotlib.pyplot as plt
import os
import re
import time
from IPython.display import clear_output
import collections

tf.__version__

D:\Anaconda3.5.20\envs\tensorflow2.0\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
D:\Anaconda3.5.20\envs\tensorflow2.0\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
D:\Anaconda3.5.20\envs\tensorflow2.0\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
D:\Anaconda3.5.20\envs\tensorflow2.0\lib\site-packages\tensorflow\pyth

'2.0.0-beta0'

In [3]:
data = pd.read_excel('Data.xlsx',delimiter="\t",error_bad_lines=False,sep=None)
data.sample(5)

Y1  Y2    Y         Domain                         area  \
45847   0  14   14            CS        Computer programming     
17424   6   3  128  biochemistry                  Immunology     
24376   5  30  102       Medical               Kidney Health     
18770   1   9   25           ECE    Analog signal processing     
14615   1  11   28           ECE         Control engineering     

                                                keywords  \
45847   Hobby-Eberly Telescope; HET; Control Systems;...   
17424   Immune tolerance; Central nervous system; Dem...   
24376   Chronic kidney disease (CKD); Awareness level...   
18770   data acquisition; analog signal processing; t...   
14615   Simulation; Virtual laboratory; Remote Labora...   

                                                Abstract  
45847  We present the development framework for the d...  
17424  In the broad field of autoimmunity and clinica...  
24376  OBJECTIVE: Chronic Kidney Disease (CKD) is a p...  
18770  In this paper, we propose a concept of a conti...  
14615  For roughly the past ten years, we have been w...

In [4]:
data.drop('Y1',axis=1, inplace=True)

In [5]:
data.drop('Y2',axis = 1,inplace = True)

data.sample(5)

Y         Domain                    area  \
34628  122       Medical        Sports Injuries     
32891  132  biochemistry      Northern blotting     
28446  118       Medical    Psoriatic Arthritis     
37955   58           MAE         Thermodynamics     
22835  128  biochemistry             Immunology     

                                                keywords  \
34628   wrist; wrist injuries; radius fractures; exte...   
32891   Erythropoietin receptor; Erythropoiesis; Canc...   
28446   Biologics; Evidence-Based Practice; Healthcar...   
37955   Corn gluten meal; Ultrasound pretreatment; He...   
22835   Colorectal neoplasms; Drug therapy; Immunolog...   

                                                Abstract  
34628  The distal radius fracture or wrist, is one of...  
32891  Testing for the presence of specific cell-surf...  
28446  Psoriasis is a complex inflammatory disorder o...  
37955  The purpose of this study was to investigate t...  
22835  Molecular pathological epidemiology (MPE) is a...

In [6]:
data.drop('Y',axis = 1,inplace = True)

data.sample(5)

Domain                                area  \
34507           ECE           Analog signal processing     
11624  biochemistry                  Southern blotting     
39890       Medical                  Children's Health     
29060       Medical                     Osteoarthritis     
17280   Psychology     Borderline personality disorder     

                                                keywords  \
34507   MSP430; EOG; HMI; Assistive technology; Signa...   
11624   Bagworm; biolistic; insect resistance; leaf d...   
39890   Families; health information; health work; de...   
29060   Ankle sprain; pain; diclofenac; menthol; topi...   
17280   ambulatory assessment; dynamic processes; eco...   

                                                Abstract  
34507  The development of assistive technologies by m...  
11624  Cowpea trypsin inhibitor (CpTI) has been repor...  
39890  This article reports findings from focus group...  
29060  Purpose This study was performed to evaluate t...  
17280  In recent years, significant technological adv...

In [7]:
domain = data.iloc[:,0]
domain = domain.values

area = data.iloc[:,1]
area = area.values

keywords = data.iloc[:,2]
keywords = keywords.values

abstract = data.iloc[:,3]
abstract = abstract.values

abstract[0]

'3-dimensional non-linear optical waves through the coherently excited resonant medium doped with the erbium atoms can be described by a 3-dimensional non-linear Schrodinger equation coupled with the self-induced transparency equations. For such a system, via the Hirota method and symbolic computation, linear forms, one-, two-and N-soliton solutions are obtained. Asymptotic analysis is conducted and suggests that the interaction between the two solitons is elastic. Bright solitons are obtained for the fields E and P, while the dark ones for the field N, with E as the electric field, P as the polarization in the resonant medium induced by the electric field, and N as the population inversion profile of the dopant atoms. Head-on interaction between the bidirectional two solitons and overtaking interaction between the unidirectional two solitons are seen. Influence of the averaged natural frequency. on the solitons are studied: (1). can affect the velocities of all the solitons; (2) Ampli

In [8]:
def unicode_to_ascii(text):
    return ''.join(c for c in unicodedata.normalize('NFD',text) if unicodedata.category(c) != 'Mn')

def process_text(text):
    
    text = unicode_to_ascii(text.lower().strip())
    # create a space between a word and the punctuation following it
    text = re.sub(r"([?.!,¿])", r" \1 ", text)
    text = re.sub(r'[" "]+', " ", text)
    # replacing everything with space except (a-z, A-Z, ".", "?", "!", ",")
    text = re.sub(r"[^a-zA-Z?.!,¿]+", " ", text)
    text = text.strip()
    
    return text

def create_dataset(text):
    
    text = [process_text(line) for line in text]
    
    return text

In [9]:
domain = create_dataset(domain)
area = create_dataset(area)
keywords = create_dataset(keywords)
abstract = create_dataset(abstract)

In [10]:
area_data = []

for line in area:
    area_data.append(line.split(' '))
area_data

[['symbolic', 'computation'],
 ['alzheimer', 's', 'disease'],
 ['green', 'building'],
 ['electric', 'motor'],
 ['parkinson', 's', 'disease'],
 ['computer', 'vision'],
 ['molecular', 'biology'],
 ['satellite', 'radio'],
 ['fluid', 'mechanics'],
 ['prenatal', 'development'],
 ['sprains', 'and', 'strains'],
 ['enzymology'],
 ['southern', 'blotting'],
 ['southern', 'blotting'],
 ['satellite', 'radio'],
 ['cancer'],
 ['enzymology'],
 ['northern', 'blotting'],
 ['sports', 'injuries'],
 ['sports', 'injuries'],
 ['senior', 'health'],
 ['computer', 'graphics'],
 ['digital', 'control'],
 ['human', 'metabolism'],
 ['polymerase', 'chain', 'reaction'],
 ['multiple', 'sclerosis'],
 ['human', 'metabolism'],
 ['human', 'metabolism'],
 ['prenatal', 'development'],
 ['northern', 'blotting'],
 ['operating', 'systems'],
 ['microcontroller'],
 ['enzymology'],
 ['attention'],
 ['immunology'],
 ['satellite', 'radio'],
 ['northern', 'blotting'],
 ['human', 'metabolism'],
 ['human', 'metabolism'],
 ['genetics'

In [11]:
keywords_data = []

for line in keywords:
    keywords_data.append(line.split(' '))

keywords_data 

[['dimensional',
  'non',
  'linear',
  'optical',
  'waves',
  'erbium',
  'doped',
  'optical',
  'fibre',
  'symbolic',
  'computation',
  'soliton',
  'solution',
  'soliton',
  'interaction'],
 ['aging',
  'tau',
  'amyloid',
  'pet',
  'alzheimer',
  's',
  'disease',
  'polypathology'],
 ['led',
  'lighting',
  'system',
  'pv',
  'system',
  'distributed',
  'lighting',
  'control',
  'energy',
  'efficiency',
  'green',
  'building',
  'daylight',
  'responsive',
  'dimming',
  'system'],
 ['ndfeb',
  'magnets',
  'electric',
  'motor',
  'electric',
  'vehicle',
  'hybrid',
  'electric',
  'vehicle',
  'recycling',
  'rare',
  'earth',
  'elements'],
 ['parkinson',
  's',
  'disease',
  'dyskinesia',
  'adenosine',
  'a',
  'a',
  'receptor',
  'striatum',
  'glutamic',
  'acid',
  'decarboxylase'],
 ['tea',
  'category',
  'identification',
  'computer',
  'vision',
  'color',
  'histogram',
  'wavelet',
  'packet',
  'entropy',
  'winner',
  'takes',
  'all',
  'radial',
  

In [12]:
abstract_data = []

for line in abstract:
    abstract_data.append(line.split(' '))
    
abstract_data

[['dimensional',
  'non',
  'linear',
  'optical',
  'waves',
  'through',
  'the',
  'coherently',
  'excited',
  'resonant',
  'medium',
  'doped',
  'with',
  'the',
  'erbium',
  'atoms',
  'can',
  'be',
  'described',
  'by',
  'a',
  'dimensional',
  'non',
  'linear',
  'schrodinger',
  'equation',
  'coupled',
  'with',
  'the',
  'self',
  'induced',
  'transparency',
  'equations',
  '.',
  'for',
  'such',
  'a',
  'system',
  ',',
  'via',
  'the',
  'hirota',
  'method',
  'and',
  'symbolic',
  'computation',
  ',',
  'linear',
  'forms',
  ',',
  'one',
  ',',
  'two',
  'and',
  'n',
  'soliton',
  'solutions',
  'are',
  'obtained',
  '.',
  'asymptotic',
  'analysis',
  'is',
  'conducted',
  'and',
  'suggests',
  'that',
  'the',
  'interaction',
  'between',
  'the',
  'two',
  'solitons',
  'is',
  'elastic',
  '.',
  'bright',
  'solitons',
  'are',
  'obtained',
  'for',
  'the',
  'fields',
  'e',
  'and',
  'p',
  ',',
  'while',
  'the',
  'dark',
  'ones',


In [13]:
Data = []
Data.append(domain)
Data

[['cs',
  'medical',
  'civil',
  'ece',
  'medical',
  'cs',
  'biochemistry',
  'ece',
  'mae',
  'psychology',
  'medical',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'ece',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'cs',
  'ece',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'psychology',
  'biochemistry',
  'cs',
  'ece',
  'biochemistry',
  'psychology',
  'biochemistry',
  'ece',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'civil',
  'civil',
  'civil',
  'mae',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'cs',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'mae',
  'cs',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'biochemistry',
  

In [14]:
for line in area_data:
    Data.append(line)
Data

[['cs',
  'medical',
  'civil',
  'ece',
  'medical',
  'cs',
  'biochemistry',
  'ece',
  'mae',
  'psychology',
  'medical',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'ece',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'cs',
  'ece',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'psychology',
  'biochemistry',
  'cs',
  'ece',
  'biochemistry',
  'psychology',
  'biochemistry',
  'ece',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'civil',
  'civil',
  'civil',
  'mae',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'cs',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'mae',
  'cs',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'biochemistry',
  

In [15]:
for line in keywords_data:
    Data.append(line)

Data

[['cs',
  'medical',
  'civil',
  'ece',
  'medical',
  'cs',
  'biochemistry',
  'ece',
  'mae',
  'psychology',
  'medical',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'ece',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'cs',
  'ece',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'psychology',
  'biochemistry',
  'cs',
  'ece',
  'biochemistry',
  'psychology',
  'biochemistry',
  'ece',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'civil',
  'civil',
  'civil',
  'mae',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'cs',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'mae',
  'cs',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'biochemistry',
  

In [16]:
for line in abstract_data:
    Data.append(line)

Data

[['cs',
  'medical',
  'civil',
  'ece',
  'medical',
  'cs',
  'biochemistry',
  'ece',
  'mae',
  'psychology',
  'medical',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'ece',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'cs',
  'ece',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'psychology',
  'biochemistry',
  'cs',
  'ece',
  'biochemistry',
  'psychology',
  'biochemistry',
  'ece',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'biochemistry',
  'civil',
  'civil',
  'civil',
  'mae',
  'medical',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'biochemistry',
  'cs',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'mae',
  'cs',
  'biochemistry',
  'biochemistry',
  'medical',
  'biochemistry',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'medical',
  'biochemistry',
  'biochemistry',
  

In [17]:
len(Data)

140956

In [18]:
from gensim.models import fasttext
import logging


In [ ]:
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
model1 = fasttext.FastText(Data,min_count=1,iter=20)
model1.save("fast_text.model")

2019-09-29 10:36:36,644 : INFO : resetting layer weights
2019-09-29 10:36:42,584 : INFO : collecting all words and their counts
2019-09-29 10:36:42,584 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-09-29 10:36:42,600 : INFO : PROGRESS: at sentence #10000, processed 65521 words, keeping 231 word types
2019-09-29 10:36:42,600 : INFO : PROGRESS: at sentence #20000, processed 84410 words, keeping 235 word types
2019-09-29 10:36:42,616 : INFO : PROGRESS: at sentence #30000, processed 102770 words, keeping 235 word types
2019-09-29 10:36:42,616 : INFO : PROGRESS: at sentence #40000, processed 121482 words, keeping 238 word types
2019-09-29 10:36:42,631 : INFO : PROGRESS: at sentence #50000, processed 167037 words, keeping 8861 word types
2019-09-29 10:36:42,663 : INFO : PROGRESS: at sentence #60000, processed 269976 words, keeping 19866 word types
2019-09-29 10:36:42,699 : INFO : PROGRESS: at sentence #70000, processed 376406 words, keeping 27390 word types


2019-09-29 10:37:58,141 : INFO : EPOCH 2 - PROGRESS: at 82.77% examples, 275464 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:37:59,142 : INFO : EPOCH 2 - PROGRESS: at 83.92% examples, 275390 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:00,159 : INFO : EPOCH 2 - PROGRESS: at 84.95% examples, 275837 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:01,189 : INFO : EPOCH 2 - PROGRESS: at 86.11% examples, 275827 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:38:02,211 : INFO : EPOCH 2 - PROGRESS: at 87.17% examples, 274408 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:03,260 : INFO : EPOCH 2 - PROGRESS: at 88.21% examples, 273132 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:04,279 : INFO : EPOCH 2 - PROGRESS: at 89.36% examples, 272282 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:05,315 : INFO : EPOCH 2 - PROGRESS: at 90.57% examples, 272228 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:38:06,318 : INFO : EPOCH 2 - PROGRESS: at 91.83% examples, 272466 words/s, in_qsiz

2019-09-29 10:39:06,465 : INFO : EPOCH 4 - PROGRESS: at 89.16% examples, 271182 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:07,481 : INFO : EPOCH 4 - PROGRESS: at 90.37% examples, 271459 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:08,499 : INFO : EPOCH 4 - PROGRESS: at 91.64% examples, 271530 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:09,516 : INFO : EPOCH 4 - PROGRESS: at 92.87% examples, 271450 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:10,534 : INFO : EPOCH 4 - PROGRESS: at 94.17% examples, 271522 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:39:11,536 : INFO : EPOCH 4 - PROGRESS: at 95.57% examples, 271751 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:12,564 : INFO : EPOCH 4 - PROGRESS: at 97.02% examples, 271524 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:13,565 : INFO : EPOCH 4 - PROGRESS: at 98.21% examples, 271347 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:39:14,602 : INFO : EPOCH 4 - PROGRESS: at 99.57% examples, 271473 words/s, in_qsiz

2019-09-29 10:40:15,020 : INFO : EPOCH 6 - PROGRESS: at 98.58% examples, 273807 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:40:16,037 : INFO : EPOCH 6 - PROGRESS: at 99.95% examples, 273971 words/s, in_qsize 2, out_qsize 1
2019-09-29 10:40:16,037 : INFO : worker thread finished; awaiting finish of 2 more threads
2019-09-29 10:40:16,068 : INFO : worker thread finished; awaiting finish of 1 more threads
2019-09-29 10:40:16,075 : INFO : worker thread finished; awaiting finish of 0 more threads
2019-09-29 10:40:16,076 : INFO : EPOCH - 6 : training on 11015535 raw words (8386112 effective words) took 30.6s, 274115 effective words/s
2019-09-29 10:40:17,104 : INFO : EPOCH 7 - PROGRESS: at 46.37% examples, 282044 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:40:18,122 : INFO : EPOCH 7 - PROGRESS: at 63.33% examples, 262147 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:40:19,123 : INFO : EPOCH 7 - PROGRESS: at 67.76% examples, 264934 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:40:20,156

2019-09-29 10:41:19,773 : INFO : EPOCH 9 - PROGRESS: at 67.79% examples, 266750 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:20,790 : INFO : EPOCH 9 - PROGRESS: at 68.93% examples, 269719 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:21,823 : INFO : EPOCH 9 - PROGRESS: at 70.15% examples, 272184 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:22,827 : INFO : EPOCH 9 - PROGRESS: at 71.09% examples, 274472 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:23,843 : INFO : EPOCH 9 - PROGRESS: at 72.01% examples, 275948 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:24,862 : INFO : EPOCH 9 - PROGRESS: at 72.95% examples, 277218 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:41:25,909 : INFO : EPOCH 9 - PROGRESS: at 74.14% examples, 277097 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:26,960 : INFO : EPOCH 9 - PROGRESS: at 75.37% examples, 277094 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:41:27,964 : INFO : EPOCH 9 - PROGRESS: at 76.60% examples, 277524 words/s, in_qsiz

2019-09-29 10:42:26,541 : INFO : EPOCH 11 - PROGRESS: at 74.14% examples, 276280 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:27,545 : INFO : EPOCH 11 - PROGRESS: at 75.34% examples, 276876 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:42:28,564 : INFO : EPOCH 11 - PROGRESS: at 76.54% examples, 276159 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:29,565 : INFO : EPOCH 11 - PROGRESS: at 77.77% examples, 276683 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:30,596 : INFO : EPOCH 11 - PROGRESS: at 79.03% examples, 276410 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:31,615 : INFO : EPOCH 11 - PROGRESS: at 80.52% examples, 276950 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:32,621 : INFO : EPOCH 11 - PROGRESS: at 81.62% examples, 276423 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:33,634 : INFO : EPOCH 11 - PROGRESS: at 82.84% examples, 276803 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:42:34,636 : INFO : EPOCH 11 - PROGRESS: at 84.00% examples, 277006 words/s

2019-09-29 10:43:34,469 : INFO : EPOCH 13 - PROGRESS: at 81.62% examples, 274763 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:35,486 : INFO : EPOCH 13 - PROGRESS: at 82.84% examples, 275138 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:36,516 : INFO : EPOCH 13 - PROGRESS: at 84.02% examples, 275417 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:37,551 : INFO : EPOCH 13 - PROGRESS: at 85.08% examples, 276188 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:43:38,554 : INFO : EPOCH 13 - PROGRESS: at 86.26% examples, 276315 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:39,571 : INFO : EPOCH 13 - PROGRESS: at 87.39% examples, 276196 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:40,588 : INFO : EPOCH 13 - PROGRESS: at 88.58% examples, 276284 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:41,590 : INFO : EPOCH 13 - PROGRESS: at 89.78% examples, 276461 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:43:42,607 : INFO : EPOCH 13 - PROGRESS: at 91.05% examples, 276521 words/s

2019-09-29 10:44:41,935 : INFO : EPOCH 15 - PROGRESS: at 89.43% examples, 273391 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:42,940 : INFO : EPOCH 15 - PROGRESS: at 90.57% examples, 273020 words/s, in_qsize 6, out_qsize 0
2019-09-29 10:44:43,957 : INFO : EPOCH 15 - PROGRESS: at 91.77% examples, 272362 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:44,975 : INFO : EPOCH 15 - PROGRESS: at 92.99% examples, 271934 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:46,008 : INFO : EPOCH 15 - PROGRESS: at 94.26% examples, 271915 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:47,025 : INFO : EPOCH 15 - PROGRESS: at 95.70% examples, 271957 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:48,059 : INFO : EPOCH 15 - PROGRESS: at 97.19% examples, 272197 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:49,093 : INFO : EPOCH 15 - PROGRESS: at 98.48% examples, 272461 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:44:50,143 : INFO : EPOCH 15 - PROGRESS: at 99.84% examples, 272500 words/s

2019-09-29 10:45:48,959 : INFO : EPOCH 17 - PROGRESS: at 93.60% examples, 267671 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:45:49,978 : INFO : EPOCH 17 - PROGRESS: at 94.88% examples, 267917 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:45:50,979 : INFO : EPOCH 17 - PROGRESS: at 96.43% examples, 268284 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:45:52,027 : INFO : EPOCH 17 - PROGRESS: at 97.77% examples, 268537 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:45:53,077 : INFO : EPOCH 17 - PROGRESS: at 99.13% examples, 268862 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:45:53,675 : INFO : worker thread finished; awaiting finish of 2 more threads
2019-09-29 10:45:53,728 : INFO : worker thread finished; awaiting finish of 1 more threads
2019-09-29 10:45:53,731 : INFO : worker thread finished; awaiting finish of 0 more threads
2019-09-29 10:45:53,733 : INFO : EPOCH - 17 : training on 11015535 raw words (8387239 effective words) took 31.2s, 269241 effective words/s
2019-09-29 10:45:

2019-09-29 10:46:54,126 : INFO : EPOCH - 19 : training on 11015535 raw words (8386867 effective words) took 30.2s, 277728 effective words/s
2019-09-29 10:46:55,148 : INFO : EPOCH 20 - PROGRESS: at 46.37% examples, 283468 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:46:56,181 : INFO : EPOCH 20 - PROGRESS: at 63.33% examples, 259734 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:46:57,200 : INFO : EPOCH 20 - PROGRESS: at 67.79% examples, 264572 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:46:58,217 : INFO : EPOCH 20 - PROGRESS: at 68.93% examples, 267359 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:46:59,250 : INFO : EPOCH 20 - PROGRESS: at 70.13% examples, 269041 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:47:00,300 : INFO : EPOCH 20 - PROGRESS: at 71.06% examples, 270201 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:47:01,319 : INFO : EPOCH 20 - PROGRESS: at 71.99% examples, 272185 words/s, in_qsize 5, out_qsize 0
2019-09-29 10:47:02,321 : INFO : EPOCH 20 - PROGRESS: at 72.92

In [ ]:
model1.wv.most_similar('area')

In [ ]:
from sklearn.decomposition import PCA

X = model1[model1.wv.vocab]

X

In [ ]:
pca = PCA(n_components=2)
result = pca.fit_transform(X)

plt.scatter(result[:,0],result[:,1])

words = list(model1.wv.vocab)

words = words[:50]

for i,word in enumerate(words):
    plt.annotate(word,xy = (result[i,0],result[i,1]))
plt.show()